# 2. Units

## Fetch prefixes name list

In [1]:
import requests
from pprint import pprint
import json
import uuid

sidf_prefixes_res_de = requests.get(
    url="https://si-digital-framework.org/SI/prefixes",
    params={"lang": "de"},
)

# Convert result to dict
sidf_prefixes_de = sidf_prefixes_res_de.json()
print(sidf_prefixes_de)
prefix_name_list = [item["label"] for item in sidf_prefixes_de]
print(prefix_name_list)

[{'label': 'quecto', 'symbol': 'q', 'scalingFactor': 1e-30, 'prefixId': 'quecto', 'scalingFactorStr': '1e-30', 'doi': 'https://doi.org/10.59161/cgpm2022res3e', 'dataType': 'http://www.w3.org/2001/XMLSchema#float', 'pid': 'https://si-digital-framework.org/SI/prefixes/quecto'}, {'label': 'ronto', 'symbol': 'r', 'scalingFactor': 1e-27, 'prefixId': 'ronto', 'scalingFactorStr': '1e-27', 'doi': 'https://doi.org/10.59161/cgpm2022res3e', 'dataType': 'http://www.w3.org/2001/XMLSchema#float', 'pid': 'https://si-digital-framework.org/SI/prefixes/ronto'}, {'label': 'yocto', 'symbol': 'y', 'scalingFactor': 1e-24, 'prefixId': 'yocto', 'scalingFactorStr': '1e-24', 'doi': 'https://doi.org/10.59161/cgpm1991res4e', 'dataType': 'http://www.w3.org/2001/XMLSchema#float', 'pid': 'https://si-digital-framework.org/SI/prefixes/yocto'}, {'label': 'zepto', 'symbol': 'z', 'scalingFactor': 1e-21, 'prefixId': 'zepto', 'scalingFactorStr': '1e-21', 'doi': 'https://doi.org/10.59161/cgpm1991res4e', 'dataType': 'http://

## Fetch all units from Qudt

In [2]:
from utils import sparql_wrapper

sparql_qudt_qk = sparql_wrapper.Sparql(
    endpoint="https://www.qudt.org/fuseki/qudt/sparql",
    src_filepath="../ontology/qudt/sparql/quantitykind.sparql",
    tgt_filepath="../ontology/qudt/data/quantitykind.json",
    debug=False,
)
qudt_qk = sparql_qudt_qk.execQuery()
# sparql_qudt_qk.writeJsonFile(data=qudt_qk)
pprint(qudt_qk)
print(len(qudt_qk))

Reading SPARQL Query from c:\Users\raeder\Desktop\dev\Gitlab\osw\apps\python-lvl2\quantities-units\src\quantities-units\utils\../ontology/qudt/sparql/quantitykind.sparql
{'head': {'vars': ['quantity', 'qlabels', 'applicableUnits', 'ucumCodes']},
 'results': {'bindings': [{'applicableUnits': {'type': 'literal',
                                               'value': 'http://qudt.org/vocab/unit/M-PER-SEC, '
                                                        'http://qudt.org/vocab/unit/CentiM-PER-HR, '
                                                        'http://qudt.org/vocab/unit/CentiM-PER-KiloYR, '
                                                        'http://qudt.org/vocab/unit/CentiM-PER-SEC, '
                                                        'http://qudt.org/vocab/unit/CentiM-PER-YR, '
                                                        'http://qudt.org/vocab/unit/GigaHZ-M, '
                                                        'http://qudt.org/vocab/unit/Ki

## Split applicableUnits into prefixedUnits and nonPrefixedUnits

In [3]:
from utils import sparql_wrapper
from pprint import pprint
import json
import requests

quant_kind_list = json.load(open("ontology/qudt/data/quantitykind.json", "r"))[
    "results"
]["bindings"]

pprint(quant_kind_list[5]["applicableUnits"])


def get_prefix_list():

    sidf_prefixes_res_de = requests.get(
        url="https://si-digital-framework.org/SI/prefixes",
        params={"lang": "de"},
    )

    # Convert result to dict
    sidf_prefixes_de = sidf_prefixes_res_de.json()
    print(sidf_prefixes_de)
    prefix_name_list = [item["label"] for item in sidf_prefixes_de]
    print(prefix_name_list)
    return prefix_name_list


prefix_name_list = get_prefix_list()


def get_unit_prefix(unit_str):
    for prefix in prefix_name_list:
        if prefix in unit_str.lower():
            return prefix
    return None


def get_non_prefixed_units_from_applicable_units(applicable_units_str):
    non_prefixed_units = []
    prefixed_units = []
    for unit_str in applicable_units_str.split(", "):

        print(unit_str)
        print(get_unit_prefix(unit_str))
        if get_unit_prefix(unit_str) == None:
            print("no prefix: ", unit_str)
            non_prefixed_units.append(unit_str)
        else:
            print("prefix: ", get_unit_prefix(unit_str), "found in ", unit_str)
            prefixed_units.append(unit_str)
    return non_prefixed_units, prefixed_units


all_prefixed_units = []
all_non_prefixed_units = []
for quant_kind in quant_kind_list:
    non_prefixed, prefixed = get_non_prefixed_units_from_applicable_units(
        quant_kind["applicableUnits"]["value"]
    )
    all_prefixed_units = all_prefixed_units + prefixed
    all_non_prefixed_units = all_non_prefixed_units + non_prefixed

all_prefixed_units = list(set(all_prefixed_units))
all_non_prefixed_units = list(set(all_non_prefixed_units))

print(len(all_prefixed_units))
print(len(all_non_prefixed_units))

{'type': 'literal', 'value': 'http://qudt.org/vocab/unit/SEC2'}
[{'label': 'quecto', 'symbol': 'q', 'scalingFactor': 1e-30, 'prefixId': 'quecto', 'scalingFactorStr': '1e-30', 'doi': 'https://doi.org/10.59161/cgpm2022res3e', 'dataType': 'http://www.w3.org/2001/XMLSchema#float', 'pid': 'https://si-digital-framework.org/SI/prefixes/quecto'}, {'label': 'ronto', 'symbol': 'r', 'scalingFactor': 1e-27, 'prefixId': 'ronto', 'scalingFactorStr': '1e-27', 'doi': 'https://doi.org/10.59161/cgpm2022res3e', 'dataType': 'http://www.w3.org/2001/XMLSchema#float', 'pid': 'https://si-digital-framework.org/SI/prefixes/ronto'}, {'label': 'yocto', 'symbol': 'y', 'scalingFactor': 1e-24, 'prefixId': 'yocto', 'scalingFactorStr': '1e-24', 'doi': 'https://doi.org/10.59161/cgpm1991res4e', 'dataType': 'http://www.w3.org/2001/XMLSchema#float', 'pid': 'https://si-digital-framework.org/SI/prefixes/yocto'}, {'label': 'zepto', 'symbol': 'z', 'scalingFactor': 1e-21, 'prefixId': 'zepto', 'scalingFactorStr': '1e-21', 'doi'

In [4]:
# Functions to extract the path of a given URL
def get_path(url):
    return url.split("/")[-1]


# def get_path_list(url_list):
#     return [get_path(url) for url in url_list]

# def get_iri_without_path(iri):
#     return iri.split("/")[:-1]


def get_main_string(unit_str, prefix_name_list):
    for prefix in prefix_name_list:
        capitalized_prefix = prefix.capitalize()
        if capitalized_prefix in unit_str:
            return unit_str.replace(capitalized_prefix, "")
    return unit_str


def merge_prefixed_and_non_prefixed_units(
    all_non_prefixed_units, all_prefixed_units, prefix_name_list
):
    unit_dict = {}
    for non_prefixed_unit in all_non_prefixed_units:
        prefixed_units = []
        # Match the non prefixed unit with all the prefixed units
        for prefixed_unit in all_prefixed_units:
            if get_path(non_prefixed_unit) == get_main_string(
                get_path(prefixed_unit), prefix_name_list
            ):
                prefixed_units.append(prefixed_unit)
        unit_dict[non_prefixed_unit] = {"prefixed_units": prefixed_units}

    return unit_dict


unit_dict = merge_prefixed_and_non_prefixed_units(
    all_non_prefixed_units, all_prefixed_units, prefix_name_list
)
pprint(unit_dict)

{'http://qudt.org/vocab/unit/A': {'prefixed_units': ['http://qudt.org/vocab/unit/KiloA',
                                                     'http://qudt.org/vocab/unit/MicroA',
                                                     'http://qudt.org/vocab/unit/MegaA',
                                                     'http://qudt.org/vocab/unit/PicoA',
                                                     'http://qudt.org/vocab/unit/MilliA']},
 'http://qudt.org/vocab/unit/A-HR': {'prefixed_units': ['http://qudt.org/vocab/unit/KiloA-HR',
                                                        'http://qudt.org/vocab/unit/MilliA-HR']},
 'http://qudt.org/vocab/unit/A-M2': {'prefixed_units': []},
 'http://qudt.org/vocab/unit/A-M2-PER-J-SEC': {'prefixed_units': []},
 'http://qudt.org/vocab/unit/A-PER-DEG_C': {'prefixed_units': []},
 'http://qudt.org/vocab/unit/A-PER-J': {'prefixed_units': []},
 'http://qudt.org/vocab/unit/A-PER-M': {'prefixed_units': ['http://qudt.org/vocab/unit/A-PER-Milli

## Fetch OSL Schema for Unit of Measure

In [5]:
from osw.core import OSW
from osw.express import OswExpress
import osw.model.entity as model


required_schemas = [
    "Category:OSW99e0f46a40ca4129a420b4bb89c4cc45",  # Unit prefix
    "Category:OSWd2520fa016844e01af0097a85bb25b25",  # Quantity Unit
]


def update_local_osw(osw_obj):
    print("fetch schemas")
    osw_obj.fetch_schema(
        OSW.FetchSchemaParam(
            schema_title=required_schemas,
            mode="replace",
        )
    )


if __name__ == "__main__":
    # Authentication
    osw_obj = OswExpress(
        domain="wiki-dev.open-semantic-lab.org",  # cred_filepath=pwd_file_path
    )
    update_local_osw(osw_obj)

c:\Users\raeder\AppData\Local\pypoetry\Cache\virtualenvs\quantities-units-W4YBs7Av-py3.12\Lib\site-packages\osw\utils\strings.py:58: FutureWarning: Possible nested set at position 16
  self.pattern = re.compile(self.pattern)
c:\Users\raeder\AppData\Local\pypoetry\Cache\virtualenvs\quantities-units-W4YBs7Av-py3.12\Lib\site-packages\osw\express.py:323: UserWarning: An exception occurred while loading the module dependencies: 
'module 'osw.model.entity' has no attribute 'File''You will be now have to connect to an OSW instance to fetch the dependencies from!
  warn(


Fetch Category:OSW11a53cdfbdc24524bf8ac435cbf65d9d
Fetch Category:OSW05b244d0a669436e96fe4e1631d5a171
Fetch Category:OSWff333fd349af4f65a69100405a9e60c7
Fetch Category:OSW2ac4493f8635481eaf1db961b63c8325
Fetch Category:Item
Fetch Category:Entity
Fetch JsonSchema:Label
Fetch JsonSchema:Label
Fetch JsonSchema:Description
Fetch JsonSchema:Statement
Fetch JsonSchema:Label
Fetch JsonSchema:Meta
Fetch Category:OSW3e3f5dd4f71842fbb8f270e511af8031
Fetch Category:OSWff333fd349af4f65a69100405a9e60c7
Fetch Category:OSW2ac4493f8635481eaf1db961b63c8325
Fetch Category:Item
Fetch Category:Entity
Fetch JsonSchema:Label
Fetch JsonSchema:Label
Fetch JsonSchema:Description
Fetch JsonSchema:Statement
Fetch JsonSchema:Label
Fetch JsonSchema:Meta
ReadAccess
AccessRestrictions
Label
Description
WikiPage
Meta
Entity
ObjectStatement
DataStatement
QuantityStatement
Item
Data
File
RemoteFile
WikiFile


c:\Users\raeder\AppData\Local\pypoetry\Cache\virtualenvs\quantities-units-W4YBs7Av-py3.12\Lib\site-packages\osw\express.py:335: UserWarning: Dependencies specified in the module 'osw.express' have been fetched from OSW:
{'LocalFile': 'Category:OSW3e3f5dd4f71842fbb8f270e511af8031', 'WikiFile': 'Category:OSW11a53cdfbdc24524bf8ac435cbf65d9d'}
Its recommended to restart the kernel, to apply all changes seamlessly.
  warn(


fetch schemas
Fetch Category:OSW99e0f46a40ca4129a420b4bb89c4cc45
Fetch Category:OSWd02741381aaa4709ae0753a0edc341ce
Fetch Category:OSWcbb09a36336740c6a2cd62db9bf647ec
Fetch Category:Item
Fetch Category:Entity
Fetch JsonSchema:Label
Fetch JsonSchema:Label
Fetch JsonSchema:Description
Fetch JsonSchema:Statement
Fetch JsonSchema:Label
Fetch JsonSchema:Meta
Fetch Category:OSW6ef70c808fb54abbbacb059c285713d4
Fetch Category:OSW93ccae36243542ceac6c951450a81d47
Fetch Category:OSWd2520fa016844e01af0097a85bb25b25
Fetch Category:Item
Fetch Category:Entity
Fetch JsonSchema:Label
Fetch JsonSchema:Label
Fetch JsonSchema:Description
Fetch JsonSchema:Statement
Fetch JsonSchema:Label
Fetch JsonSchema:Meta
Fetch Category:OSW6ef70c808fb54abbbacb059c285713d4
Fetch Category:OSW93ccae36243542ceac6c951450a81d47
Fetch Category:OSW6ef70c808fb54abbbacb059c285713d4
Fetch Category:OSW93ccae36243542ceac6c951450a81d47
ReadAccess
AccessRestrictions
Label
Description
WikiPage
Meta
Characteristic
OntologyRelated
Entit

## Instanciate Example Unit of Measure

In [6]:
title = "Item:OSWc73852e7049f42e7b5282866f3839f5e"  # Meter
meter_u = osw_obj.load_entity(title)

pprint(meter_u)

Fetch Category:OSW7199b9568d96476cacfe30060c64f371
Fetch Category:OSWd2520fa016844e01af0097a85bb25b25
Fetch Category:Item
Fetch Category:Entity
Fetch JsonSchema:Label
Fetch JsonSchema:Label
Fetch JsonSchema:Description
Fetch JsonSchema:Statement
Fetch JsonSchema:Label
Fetch JsonSchema:Meta
Fetch Category:OSW6ef70c808fb54abbbacb059c285713d4
Fetch Category:OSW93ccae36243542ceac6c951450a81d47
Fetch Category:OSW6ef70c808fb54abbbacb059c285713d4
Fetch Category:OSW93ccae36243542ceac6c951450a81d47
ReadAccess
AccessRestrictions
Label
Description
WikiPage
Meta
Characteristic
OntologyRelated
Entity
ObjectStatement
DataStatement
QuantityStatement
Item
IntangibleItem
Enumeration
PrefixUnit
BaseUnitOfMeasure(type=['Category:OSW7199b9568d96476cacfe30060c64f371'], uuid=UUID('c73852e7-049f-42e7-b528-2866f3839f5e'), exact_ontology_match=['https://qudt.org/vocab/unit/M', 'https://si-digital-framework.org/SI/units/metre', ' http://dbpedia.org/resource/Metre ', 'http://www.ontology-of-units-of-measure.org/

## Fetch Units from Ontology and complete properties of unit dictionary

In [7]:
from utils import sparql_wrapper
from pprint import pprint

sparql_qudt_unit_params = sparql_wrapper.Sparql(
    endpoint="https://www.qudt.org/fuseki/qudt/sparql",
    src_filepath="../ontology/qudt/sparql/units.sparql",
    tgt_filepath="../ontology/qudt/data/units.json",
    debug=False,
)
qudt_units_param_res = sparql_qudt_unit_params.execQuery()
sparql_qudt_unit_params.writeJsonFile(data=qudt_units_param_res)
print(
    f"num results.bindings: {len(qudt_units_param_res['results']['bindings'])}"
)
pprint(qudt_units_param_res)

Reading SPARQL Query from c:\Users\raeder\Desktop\dev\Gitlab\osw\apps\python-lvl2\quantities-units\src\quantities-units\utils\../ontology/qudt/sparql/units.sparql
Writing JSON data to c:\Users\raeder\Desktop\dev\Gitlab\osw\apps\python-lvl2\quantities-units\src\quantities-units\utils\../ontology/qudt/data/units.json
num results.bindings: 950
{'head': {'vars': ['applicableUnit',
                   'dimensionVector',
                   'symbol',
                   'conversionMultiplierSN',
                   'dbpediaMatch',
                   'siExactMatch',
                   'plainTextDescription',
                   'description',
                   'ucumCodes',
                   'applicableSystems',
                   'qlabels']},
 'results': {'bindings': [{'applicableSystems': {'type': 'literal',
                                                 'value': 'http://qudt.org/vocab/sou/SI, '
                                                          'http://qudt.org/vocab/sou/CGS, '
      

In [8]:
# from jsonpath_ng import jsonpath, parse

# # use json path to extract all another info of same level in results.bindings where the identifier is results.bindings[*].applicableUnit.value and the value is "http://qudt.org/vocab/unit#Meter"
# jsonpath_expr = parse(
#     "$.results.bindings[?(@.applicableUnit.value == 'http://qudt.org/vocab/unit#Meter')]"
# )
# meter_unit_info = [match.value for match in jsonpath_expr.find(qudt_units_param_res)]

from jsonpath_ng.ext import parse
import uuid

# Use json path to extract all another info of same level in results.bindings where the identifier is results.bindings[*].applicableUnit.value and the value is "http://qudt.org/vocab/unit#Meter"
jsonpath_expr = parse(
    '$.results.bindings[?(@.applicableUnit.value = "http://qudt.org/vocab/unit/MilliPA-SEC")]'
)
# meter_unit_info = [match.value for match in jsonpath_expr.find(qudt_units_param_res)]
# pprint(meter_unit_info)

pprint(jsonpath_expr.find(qudt_units_param_res)[0].value)


def match_json_path_key(qudt_units_param_res, identifier="", key=""):
    jsonpath_expr = parse(
        f'$.results.bindings[?(@.applicableUnit.value = "{identifier}")].{key}.value'
    )
    return jsonpath_expr.find(qudt_units_param_res)[0].value


def match_object_json_path(qudt_units_param_res=None, identifier=""):
    # print(f"IDENTIFIER: {identifier}")
    jsonpath_expr = parse(
        f'$.results.bindings[?(@.applicableUnit.value = "{identifier}")]'
    )

    return jsonpath_expr.find(qudt_units_param_res)[0].value


def get_prefix_uuid(data=[], prefix=""):
    jsonpath_expr = parse(f'$[?(@.label = "{prefix}")].pid')
    return uuid.uuid5(
        namespace=uuid.NAMESPACE_URL, name=jsonpath_expr.find(data)[0].value
    )


# test
# pprint(
#     match_json_path_key(
#         qudt_units_param_res,
#         identifier="http://qudt.org/vocab/unit/KiloBYTE",
#         key="ucumCodes",
#     )
# )

pprint(
    match_object_json_path(
        qudt_units_param_res=qudt_units_param_res,
        identifier="http://qudt.org/vocab/unit/KiloBYTE",
    )
)

pprint(get_prefix_uuid(sidf_prefixes_de, "kilo"))

{'applicableSystems': {'type': 'literal',
                       'value': 'http://qudt.org/vocab/sou/SI, '
                                'http://qudt.org/vocab/sou/CGS, '
                                'http://qudt.org/vocab/sou/CGS-EMU, '
                                'http://qudt.org/vocab/sou/CGS-GAUSS'},
 'applicableUnit': {'type': 'uri',
                    'value': 'http://qudt.org/vocab/unit/MilliPA-SEC'},
 'conversionMultiplierSN': {'datatype': 'http://www.w3.org/2001/XMLSchema#double',
                            'type': 'literal',
                            'value': '0.001e0'},
 'description': {'datatype': 'http://www.w3.org/1999/02/22-rdf-syntax-ns#HTML',
                 'type': 'literal',
                 'value': '0.001-fold of the product of the SI derived unit '
                          'pascal and the SI base unit second'},
 'dimensionVector': {'type': 'uri',
                     'value': 'http://qudt.org/vocab/dimensionvector/A0E0L-1I0M1H0T-1D0'},
 'plainTextDe

## Map Attributes from Ontology Data to OSL Schema

In [9]:
import uuid

units = []


def dict_from_comma_separated_list(qlabel):
    parts = qlabel.split(", ")
    ret = {}
    for part in parts:
        value, key = part.split("@")
        ret[key] = value
    return ret


def get_osw_prefix_unit(
    qudt_units_param_res=None, prefixes_list=None, url=None, parent_uuid=None
):

    prefix_unit_dict = match_object_json_path(
        qudt_units_param_res=qudt_units_param_res,
        identifier=url,
    )
    # print(prefix_unit_dict)
    ontology_match_list = [prefix_unit_dict["applicableUnit"]["value"]]
    # print("dbpediaMatch" in prefix_unit_dict.keys())
    # print(prefix_unit_dict.keys())
    if "dbpediaMatch" in prefix_unit_dict.keys():
        ontology_match_list.append(prefix_unit_dict["dbpediaMatch"]["value"])
        # print(prefix_unit_dict["dbpediaMatch"]["value"])
    if "siExactMatch" in prefix_unit_dict:
        ontology_match_list.append(prefix_unit_dict["siExactMatch"]["value"])
    conversion_multiplier = None
    if "conversionMultiplierSN" in prefix_unit_dict:

        conversion_multiplier = prefix_unit_dict["conversionMultiplierSN"][
            "value"
        ]
        # print(conversion_multiplier)

    _uuid = str(uuid.uuid5(namespace=uuid.NAMESPACE_URL, name=url))
    # print(_uuid)
    prefix_unit = model.PrefixUnit(
        uuid=_uuid,
        osw_id="Item:OSW"
        + str(parent_uuid).replace("-", "")
        + "#OSW"
        + _uuid.replace("-", ""),
        prefix="Item:OSW"
        + str(get_prefix_uuid(prefixes_list, get_unit_prefix(url))).replace(
            "-", ""
        ),
        # prefix_symbol="",  # Causes edge case error
        main_symbol=match_json_path_key(
            qudt_units_param_res,
            identifier=url,
            key="symbol",
        ),
        exact_ontology_match=ontology_match_list,
        conversion_factor_from_si=conversion_multiplier,
        description=[{"text": "Description", "lang": "en"}],
    )

    return prefix_unit


i = 0
# Iteration over the unit_dict to create the QuantityUnit objects
for non_prefixed_unit_iri, unit_property_dict in unit_dict.items():
    name = non_prefixed_unit_iri.split("/")[-1]

    match_unit_dict = match_object_json_path(
        qudt_units_param_res=qudt_units_param_res,
        identifier=non_prefixed_unit_iri,
    )
    ontology_match_list = [match_unit_dict["applicableUnit"]["value"]]
    if "dbpediaMatch" in match_unit_dict.keys():
        ontology_match_list.append(match_unit_dict["dbpediaMatch"]["value"])
    if "siExactMatch" in match_unit_dict:
        ontology_match_list.append(match_unit_dict["siExactMatch"]["value"])
    conversion_multiplier = None
    if "conversionMultiplierSN" in match_unit_dict:
        conversion_multiplier = match_unit_dict["conversionMultiplierSN"][
            "value"
        ]
    # sequence of description before plainTextDescription is essential for overwriting
    description_list = None
    plainTextDescription = None
    if "description" in match_unit_dict:
        plainTextDescription = match_unit_dict["description"]["value"]
        description_list = [
            model.Description(
                text=plainTextDescription,
                lang="en",
            )
        ]
        # print(description_list)
    # overwrite description if plainTextDescription is present
    if "plainTextDescription" in match_unit_dict:
        plainTextDescription = match_unit_dict["plainTextDescription"]["value"]
        description_list = [
            model.Description(
                text=plainTextDescription,
                lang="en",
            )
        ]
        # print(description_list)
    if description_list == None:
        i += 1
        # print("No description found for ", name)

    qlabels = match_json_path_key(
        qudt_units_param_res,
        identifier=non_prefixed_unit_iri,
        key="qlabels",
    )

    label_dict = dict_from_comma_separated_list(qlabels)
    ### clean missing "en"
    if "" in label_dict.keys():
        label_dict["en"] = label_dict[""]
        del label_dict[""]

    osw_label_list = [
        model.Label(text=value, lang=key) for key, value in label_dict.items()
    ]
    symbol = match_json_path_key(
        qudt_units_param_res,
        identifier=non_prefixed_unit_iri,
        key="symbol",
    )
    _uuid = uuid.uuid5(
        namespace=uuid.NAMESPACE_URL, name=non_prefixed_unit_iri
    )
    # print(_uuid)
    prefix_unit_list = [
        get_osw_prefix_unit(
            qudt_units_param_res=qudt_units_param_res,
            prefixes_list=sidf_prefixes_de,
            url=url,
            parent_uuid=_uuid,
        )
        for url in unit_property_dict["prefixed_units"]
    ]

    unit = model.QuantityUnit(
        uuid=_uuid,
        exact_ontology_match=ontology_match_list,
        name=name,
        label=osw_label_list,
        main_symbol=symbol,
        prefix_units=prefix_unit_list,
        description=description_list,
        conversion_factor_from_si=conversion_multiplier,
    )
    units.append(unit)

pprint(units)
print("not described units couter: ", i)

[QuantityUnit(type=['Category:OSWd2520fa016844e01af0097a85bb25b25'], uuid=UUID('58a109c7-b242-5676-9e6f-6716407aff58'), exact_ontology_match=['http://qudt.org/vocab/unit/MOL-PER-L'], close_ontology_match=None, rdf_type=None, iri=None, name='MOL-PER-L', label=[Label(text='Mole per Litre', lang='en')], short_name=None, query_label=None, description=[Description(text='SI base unit mol divided by the unit litre', lang='en')], image=None, ordering_categories=None, keywords=None, based_on=None, statements=None, attachments=None, meta=None, entry_access=None, main_symbol='mol/L', conversion_factor_from_si=1000.0, prefix_units=[PrefixUnit(type=['Category:OSW6ef70c808fb54abbbacb059c285713d4'], uuid='6c417325-ca15-5276-b312-fd6393406a04', exact_ontology_match=['http://qudt.org/vocab/unit/FemtoMOL-PER-L'], close_ontology_match=None, osw_id='Item:OSW58a109c7b24256769e6f6716407aff58#OSW6c417325ca155276b312fd6393406a04', conversion_factor_from_si=1e-12, prefix='Item:OSWaa15a848c6445a7087c7293dd18a72

## Upload Units to DEV WIKI

In [11]:
# Test of single unit
test_unit = units[6]
pprint(test_unit.dict())

from osw.core import OSW

# Upload single unit to OSW
# osw_obj.delete_entity(test_unit)
# osw_obj.store_entity(test_unit)

# Upload all units to OSW
# osw_obj.delete_entity(units)
# osw_obj.store_entity(units)
osw_obj.store_entity(OSW.StoreEntityParam(entities=units, overwrite=True))

{'attachments': None,
 'based_on': None,
 'close_ontology_match': None,
 'conversion_factor_from_si': 1.157407e-05,
 'description': [{'lang': 'en',
                  'text': 'power of the SI base unit metre with the exponent 3 '
                          'divided by the unit day'}],
 'entry_access': None,
 'exact_ontology_match': ['http://qudt.org/vocab/unit/M3-PER-DAY'],
 'image': None,
 'iri': None,
 'keywords': None,
 'label': [{'lang': 'en', 'text': 'Cubic Metre per Day'}],
 'main_symbol': 'm³/day',
 'meta': None,
 'name': 'M3-PER-DAY',
 'ordering_categories': None,
 'prefix_units': [{'close_ontology_match': None,
                   'conversion_factor_from_si': 1.157407e-11,
                   'exact_ontology_match': ['http://qudt.org/vocab/unit/CentiM3-PER-DAY'],
                   'main_symbol': 'cm³/day',
                   'osw_id': 'Item:OSW689f8c6a489355daaad85c99ffcc2a52#OSWb7fd7c05c5355fccaec605b426f8e1c7',
                   'prefix': 'Item:OSWbca49386a57457c1a1b250da355d9